In [1]:
from urllib.parse import urlencode, quote_plus
from urllib.request import urlopen, Request
import pandas as pd
import json, xmltodict
import pandas_profiling

service_key = 'VtS0z8ILedUMwjLe4kgmh6T8MWir/F9BsncSDqxFPsMsJaeTDkw3fDhNisjV5GdZerEeaEhxwDYbDhRG2SDz1g=='

In [5]:
def get_standard_price(ldCode, stdrYear, numOfRows, pageNo):
    queryParams = '?' + urlencode({ quote_plus('ServiceKey') : service_key, quote_plus('ldCode') : ldCode, quote_plus('stdrYear') : stdrYear, quote_plus('format') : 'json', quote_plus('numOfRows') : numOfRows, quote_plus('pageNo') : pageNo })
    
    url = 'http://apis.data.go.kr/1611000/nsdi/ReferLandPriceService/attr/getReferLandPriceAttr'
    request = Request(url + queryParams)
    request.get_method = lambda: 'GET'
    response_body = urlopen(request).read().decode('utf-8')
    data = json.loads(response_body)
    
    return data

In [2]:
def get_gongdong_price(pnu, stdrYear, numOfRows, pageNo):    
    queryParams = '?' + urlencode({ quote_plus('ServiceKey') : service_key, quote_plus('pnu') : pnu, quote_plus('stdrYear') : stdrYear, quote_plus('format') : 'json', quote_plus('numOfRows') : numOfRows, quote_plus('pageNo') : pageNo })
    
    url = 'http://apis.data.go.kr/1611000/nsdi/ApartHousingPriceService/attr/getApartHousingPriceAttr'
    request = Request(url + queryParams)
    request.get_method = lambda: 'GET'
    response_body = urlopen(request).read().decode('utf-8')
    data = json.loads(response_body)
    
    return data

In [10]:
def get_price_sh(LAWD_CD, DEAL_YMD):
    queryParams = '?' + urlencode({ quote_plus('ServiceKey') : service_key, quote_plus('LAWD_CD') : LAWD_CD, quote_plus('DEAL_YMD') : DEAL_YMD })

    url_sh = 'http://openapi.molit.go.kr:8081/OpenAPI_ToolInstallPackage/service/rest/RTMSOBJSvc/getRTMSDataSvcSHTrade'
    request = Request(url_sh + queryParams)
    request.get_method = lambda: 'GET'
    response_body = urlopen(request).read().decode('utf-8')
    data = json.loads(json.dumps(xmltodict.parse(response_body)))
    
    return data

In [3]:
def get_price_yeonrib(LAWD_CD, DEAL_YMD):
    queryParams = '?' + urlencode({ quote_plus('ServiceKey') : service_key, quote_plus('LAWD_CD') : LAWD_CD, quote_plus('DEAL_YMD') : DEAL_YMD })

    url_yeonrib = 'http://openapi.molit.go.kr:8081/OpenAPI_ToolInstallPackage/service/rest/RTMSOBJSvc/getRTMSDataSvcRHTrade'
    request = Request(url_yeonrib + queryParams)
    request.get_method = lambda: 'GET'
    response_body = urlopen(request).read().decode('utf-8')
    data = json.loads(json.dumps(xmltodict.parse(response_body)))
    
    return data

In [12]:
def get_price_officetel(LAWD_CD, DEAL_YMD):
    queryParams = '?' + urlencode({ quote_plus('ServiceKey') : service_key, quote_plus('LAWD_CD') : LAWD_CD, quote_plus('DEAL_YMD') : DEAL_YMD })

    url_officetel = 'http://openapi.molit.go.kr/OpenAPI_ToolInstallPackage/service/rest/RTMSOBJSvc/getRTMSDataSvcOffiTrade'
    request = Request(url_officetel + queryParams)
    request.get_method = lambda: 'GET'
    response_body = urlopen(request).read().decode('utf-8')
    data = json.loads(json.dumps(xmltodict.parse(response_body)))
    
    return data

In [4]:
data2 = get_price_yeonrib('11110', '201712')
df2 = pd.DataFrame(data2['response']['body']['items']['item'])
df2.head()

거래금액  건축년도     년  대지권면적  법정동      연립다세대   월      일   전용면적       지번  \
0  39,600  2017  2017  39.35  신교동      팔라디오빌  12  21~31  55.63    17-10   
1  51,000  2000  2017  42.74  창성동      이본팔레스  12   1~10  74.77     98-2   
2  31,800  2002  2017  30.08  누상동    코디골드빌C동  12  11~20  59.97   151-15   
3  30,000  1999  2017  29.74  누상동  녹원하이츠빌라6동  12  21~31  59.79  166-247   
4  48,000  2002  2017  36.13  누상동      진영하이빌  12  21~31  78.69     33-1   

    지역코드  층  
0  11110  4  
1  11110  4  
2  11110  4  
3  11110  4  
4  11110  3

In [5]:
code_df = pd.read_csv('/Users/jungwookim/dev/RealEstateInSeoul/beob_code.csv', encoding = "utf-8", index_col='법정동코드')
code_dic = code_df.loc[:,['법정동명']].to_dict()['법정동명']

seoul_code_list = list()
seoul_code_10 = dict()
for code in code_dic:
    if code < 2000000000:
        seoul_code_10[code] = code_dic[code]
        
for key in seoul_code_10:
    seoul_code_list.append((str(key)[:5], str(key)[5:], seoul_code_10[key]))

In [6]:
province_list = list()
for item in seoul_code_list:
    if item[0] not in province_list:
        province_list.append(item[0])

In [7]:
import os

# if not os.path.exists('/Users/jungwookim/dev/damta/real_estate/'):
#     os.makedirs('/Users/jungwookim/dev/damta/real_estate/')

with open('/Users/jungwookim/dev/RealEstateInSeoul/yeonrib.csv', 'a') as f:
    df_temp = pd.DataFrame(columns=df2.columns)
    df_temp.to_csv('yeonrib.csv', index=False)

    date_set = [str(x) for x in range(201701, 201713)]
    
    for date in date_set:
        for item in province_list:
            try:
                # 여기서 코드는 구까지 있는 5-digits 코드이다.
                data = get_price_yeonrib(item, date)
                dataFrame = pd.DataFrame(data['response']['body']['items']['item'])
                dataFrame.to_csv(f, header=False, columns=dataFrame.columns)
                print(item, date)
            except:
                print('NOPE')
                continue

NOPE
11110 201701
11140 201701
11170 201701
11200 201701
11215 201701
11230 201701
11260 201701
11290 201701
11305 201701
11320 201701
11350 201701
11380 201701
11410 201701
11440 201701
11470 201701
11500 201701
11530 201701
11545 201701
11560 201701
11590 201701
11620 201701
11650 201701
11680 201701
11710 201701
11740 201701
NOPE
11110 201702
11140 201702
11170 201702
11200 201702
11215 201702
11230 201702
11260 201702
11290 201702
11305 201702
11320 201702
11350 201702
11380 201702
11410 201702
11440 201702
11470 201702
11500 201702
11530 201702
11545 201702
11560 201702
11590 201702
11620 201702
11650 201702
11680 201702
11710 201702
11740 201702
NOPE
11110 201703
11140 201703
11170 201703
11200 201703
11215 201703
11230 201703
11260 201703
11290 201703
11305 201703
11320 201703
11350 201703
11380 201703
11410 201703
11440 201703
11470 201703
11500 201703
11530 201703
11545 201703
11560 201703
11590 201703
11620 201703
11650 201703
11680 201703
11710 201703
11740 201703
NOPE
11110

In [9]:
df2 = pd.read_csv('yeonrib.csv')

In [44]:
df2.iloc[18503, :]

거래금액      10,000
건축년도        1993
년           2017
대지권면적      22.36
법정동          녹번동
연립다세대    삼환하이츠맨션
월              5
일          21~31
전용면적        47.4
지번        120-52
지역코드       11380
층              1
Name: 55, dtype: object

In [49]:
def remove_nan_rows(df):
    remove_index = list()
    for n, item in enumerate(pd.isnull(df['법정동']).values):
        if item:
            remove_index.append(n)

    print(remove_index, "의 인덱스 rows가 삭제되었습니다.")
    df.drop(df.index[remove_index], inplace=True)

In [50]:
remove_nan_rows(df2)

[] 의 인덱스 rows가 삭제되었습니다.


In [36]:
remove_nan_rows(df2)

[18503] 의 인덱스 rows가 삭제되었습니다.


In [58]:
get_address(seoul_code_list)

[('11110', '서울특별시 종로구', '00000', ''),
 ('11110', '서울특별시 종로구', '10100', '청운동'),
 ('11110', '서울특별시 종로구', '10200', '신교동'),
 ('11110', '서울특별시 종로구', '10300', '궁정동'),
 ('11110', '서울특별시 종로구', '10400', '효자동'),
 ('11110', '서울특별시 종로구', '10500', '창성동'),
 ('11110', '서울특별시 종로구', '10600', '통의동'),
 ('11110', '서울특별시 종로구', '10700', '적선동'),
 ('11110', '서울특별시 종로구', '10800', '통인동'),
 ('11110', '서울특별시 종로구', '10900', '누상동'),
 ('11110', '서울특별시 종로구', '11000', '누하동'),
 ('11110', '서울특별시 종로구', '11100', '옥인동'),
 ('11110', '서울특별시 종로구', '11200', '체부동'),
 ('11110', '서울특별시 종로구', '11300', '필운동'),
 ('11110', '서울특별시 종로구', '11400', '내자동'),
 ('11110', '서울특별시 종로구', '11500', '사직동'),
 ('11110', '서울특별시 종로구', '11600', '도렴동'),
 ('11110', '서울특별시 종로구', '11700', '당주동'),
 ('11110', '서울특별시 종로구', '11800', '내수동'),
 ('11110', '서울특별시 종로구', '11900', '세종로'),
 ('11110', '서울특별시 종로구', '12000', '신문로1가'),
 ('11110', '서울특별시 종로구', '12100', '신문로2가'),
 ('11110', '서울특별시 종로구', '12200', '청진동'),
 ('11110', '서울특별시 종로구', '12300', '서린동'),
 ('11110', '서울특

In [57]:
def get_address(code_list):
    address_list = list()
    for item in code_list:
        # ~구라고 되어있는 곳까지 짜르고
        if item[2].count('구') >= 1:
            split_point = item[2].rfind('구')
            tp = (item[0], item[2][:split_point+1], item[1], item[2][split_point+1:].replace(" ", ""))
            address_list.append(tp)
        else:
            continue
    return address_list

In [89]:
address_list[4][3] == '동'

False

In [75]:
print(type(address_list[4][2]))

<class 'str'>


In [91]:
for a, b in df2.iterrows():
    
    print(b['지역코드'])
#     if (b['법정동'] is address_list[4][3]):
#         print(b['법정동'])

11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
11200
1120

11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11470
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
1150

11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
1130

11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11545
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11560
11590
11590
11590
11590
11590
11590
11590
11590
11590
11590
11590
11590
11590
11590
11590
11590
11590
11590
11590
11590
1159

11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11290
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
11305
1130

11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
11500
1150

11740
11740
11740
11740
11740
11740
11740
11740
11740
11740
11740
11740
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11110
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11140
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
11170
1117

11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11380
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
11410
1141

11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11650
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
11680
1168

KeyboardInterrupt: 

In [90]:
get_address(seoul_code_list)

[('11110', '서울특별시 종로구', '00000', ''),
 ('11110', '서울특별시 종로구', '10100', '청운동'),
 ('11110', '서울특별시 종로구', '10200', '신교동'),
 ('11110', '서울특별시 종로구', '10300', '궁정동'),
 ('11110', '서울특별시 종로구', '10400', '효자동'),
 ('11110', '서울특별시 종로구', '10500', '창성동'),
 ('11110', '서울특별시 종로구', '10600', '통의동'),
 ('11110', '서울특별시 종로구', '10700', '적선동'),
 ('11110', '서울특별시 종로구', '10800', '통인동'),
 ('11110', '서울특별시 종로구', '10900', '누상동'),
 ('11110', '서울특별시 종로구', '11000', '누하동'),
 ('11110', '서울특별시 종로구', '11100', '옥인동'),
 ('11110', '서울특별시 종로구', '11200', '체부동'),
 ('11110', '서울특별시 종로구', '11300', '필운동'),
 ('11110', '서울특별시 종로구', '11400', '내자동'),
 ('11110', '서울특별시 종로구', '11500', '사직동'),
 ('11110', '서울특별시 종로구', '11600', '도렴동'),
 ('11110', '서울특별시 종로구', '11700', '당주동'),
 ('11110', '서울특별시 종로구', '11800', '내수동'),
 ('11110', '서울특별시 종로구', '11900', '세종로'),
 ('11110', '서울특별시 종로구', '12000', '신문로1가'),
 ('11110', '서울특별시 종로구', '12100', '신문로2가'),
 ('11110', '서울특별시 종로구', '12200', '청진동'),
 ('11110', '서울특별시 종로구', '12300', '서린동'),
 ('11110', '서울특

In [139]:
# dongCode 추가

address_list = get_address(seoul_code_list)
dong_list = list()
for a, row in df2.iterrows():
    for item in address_list:
        if str(row['지역코드']) in item[0]:
            if str(row['법정동']) in item[3]:
                dong_list.append(item[2])
                break
            

청운동 청운동
청운동 청운동
효자동 효자동
통인동 통인동
누상동 누상동
누상동 누상동
누상동 누상동
누상동 누상동
누상동 누상동
옥인동 옥인동
옥인동 옥인동
필운동 필운동
삼청동 삼청동
원서동 원서동
연건동 연건동
혜화동 혜화동
혜화동 혜화동
명륜1가 명륜1가
명륜3가 명륜3가
명륜3가 명륜3가
명륜3가 명륜3가
명륜3가 명륜3가
명륜3가 명륜3가
명륜3가 명륜3가
창신동 창신동
창신동 창신동
창신동 창신동
숭인동 숭인동
숭인동 숭인동
숭인동 숭인동
숭인동 숭인동
행촌동 행촌동
행촌동 행촌동
평창동 평창동
평창동 평창동
평창동 평창동
평창동 평창동
평창동 평창동
평창동 평창동
부암동 부암동
홍지동 홍지동
신영동 신영동
신영동 신영동
신영동 신영동
신영동 신영동
신영동 신영동
신영동 신영동
신영동 신영동
무악동 무악동
남산동2가 남산동2가
필동2가 필동2가
신당동 신당동
신당동 신당동
신당동 신당동
신당동 신당동
신당동 신당동
신당동 신당동
신당동 신당동
신당동 신당동
신당동 신당동
신당동 신당동
신당동 신당동
신당동 신당동
신당동 신당동
신당동 신당동
신당동 신당동
황학동 황학동
후암동 후암동
후암동 후암동
후암동 후암동
후암동 후암동
후암동 후암동
후암동 후암동
후암동 후암동
후암동 후암동
후암동 후암동
후암동 후암동
후암동 후암동
후암동 후암동
후암동 후암동
후암동 후암동
후암동 후암동
용산동2가 용산동2가
용산동2가 용산동2가
용산동2가 용산동2가
용산동2가 용산동2가
용산동2가 용산동2가
청파동1가 청파동1가
청파동1가 청파동1가
청파동1가 청파동1가
청파동1가 청파동1가
청파동1가 청파동1가
청파동2가 청파동2가
원효로1가 원효로1가
원효로1가 원효로1가
신창동 신창동
효창동 효창동
효창동 효창동
효창동 효창동
용문동 용문동
용문동 용문동
용문동 용문동
용문동 용문동
용문동 용문동
용문동 용문동
신계동 신계동
한강로1가 한강로1가
한강로1가 한강로1가
이촌동 이촌동
이태원동 이태원동
이태원동 이태원동
이태원동 이태원동
이태원동 이태원동
한남동 한남동


홍은동 홍은동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
북가좌동 북가좌동
남가좌동 남가좌동
남가좌동 남가좌동
남가좌동 남가좌동
남가좌동 남가좌동
남가좌동 남가좌동
남가좌동 남가좌동
남가좌동 남가좌동
남가좌동 남가좌동
아현동 아현동
아현동 아현동
아현동 아현동
아현동 아현동
아현동 아현동
아현동 아현동
아현동 아현동
아현동 아현동
아현동 아현동
아현동 아현동
아현동 아현동
아현동 아현동
아현동 아현동
아현동 아현동
아현동 아현동
아현동 아현동
공덕동 공덕동
공덕동 공덕동
공덕동 공덕동
공덕동 공덕동
용강동 용강동
마포동 마포동
마포동 마포동
염리동 염리동
염리동 염리동
신수동 신수동
신수동 신수동
상수동 상수동
상수동 상수동
서교동 서교동
서교동 서교동
서교동 서교동
서교동 서교동
서교동 서교동
서교동 서교동
서교동 서교동
서교동 서교동
서교동 서교동
서교동 서교동
서교동 서교동
서교동 서교동
서교동 서교동
동교동 동교동
합정동 합정동
합정동 합정동
합정동 합정동
합정동 합정동
합정동 합정동
합정동 합정동
합정동 합정동
합정동 합정동
합정동 합정동
합정동 합정동
합정동 합정동
합정동 합정동
합정동 합정동
합정동 합정동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 망원동
망원동 

방이동 방이동
방이동 방이동
방이동 방이동
방이동 방이동
방이동 방이동
방이동 방이동
방이동 방이동
방이동 방이동
방이동 방이동
방이동 방이동
방이동 방이동
방이동 방이동
방이동 방이동
오금동 오금동
오금동 오금동
오금동 오금동
오금동 오금동
오금동 오금동
오금동 오금동
오금동 오금동
오금동 오금동
오금동 오금동
오금동 오금동
거여동 거여동
거여동 거여동
거여동 거여동
거여동 거여동
거여동 거여동
거여동 거여동
거여동 거여동
거여동 거여동
거여동 거여동
마천동 마천동
마천동 마천동
마천동 마천동
마천동 마천동
마천동 마천동
마천동 마천동
마천동 마천동
마천동 마천동
마천동 마천동
명일동 명일동
고덕동 고덕동
고덕동 고덕동
고덕동 고덕동
고덕동 고덕동
상일동 상일동
상일동 상일동
상일동 상일동
길동 길동
길동 길동
길동 길동
길동 길동
길동 길동
길동 길동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
암사동 암사동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
성내동 성내동
천호동 천호동
천호동 천호동
천호동 천호동
천호동 천호동
천호동 천호동
천호동 천호동
천호동 천호동
천호동 

방학동 방학동
방학동 방학동
방학동 방학동
방학동 방학동
방학동 방학동
방학동 방학동
방학동 방학동
방학동 방학동
방학동 방학동
방학동 방학동
방학동 방학동
방학동 방학동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
월계동 월계동
월계동 월계동
월계동 월계동
월계동 월계동
월계동 월계동
월계동 월계동
월계동 월계동
월계동 월계동
월계동 월계동
월계동 월계동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
하계동 하계동
하계동 하계동
하계동 하계동
하계동 하계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계

목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월

...

창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
창동 창동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
도봉동 도봉동
월계동 월계동
월계동 월계동
월계동 월계동
월계동 월계동
월계동 월계동
월계동 월계동
월계동 월계동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
공릉동 공릉동
하계동 하계동
하계동 하계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
상계동 상계동
중계동 중계동
중계동 중계동
중계동 중계동
수색동 수색동
수색동 수색동
수색동 수색동
수색동 수색동
수색동 수색동
수색동 수색동
수색동 수색동
수색동 수색동
수색동 수색동
수색동 수색동
수색동 수색동
수색동 수색동
수색동 수색동
수색동 수색동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
녹번동 녹번동
불광동 불광동


궁동 궁동
궁동 궁동
온수동 온수동
온수동 온수동
천왕동 천왕동
천왕동 천왕동
항동 항동
항동 항동
항동 항동
항동 항동
가산동 가산동
가산동 가산동
가산동 가산동
가산동 가산동
가산동 가산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
독산동 독산동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
시흥동 시흥동
영등포동 영등포동
영등포동1가 영등포동1가
영등포동1가 영등포동1가
영등포동1가 영등포동1가
영등포동2가 영등포동2가
영등포동6가 영등포동6가
영등포동7가 영등포동7가
영등포동7가 영등포동7가
당산동3가 당산동3가
당산동4가 당산동4가
당산동 당산동
도림동 도림동
양평동1가 양평동1가
양평동1

중곡동 중곡동
중곡동 중곡동
중곡동 중곡동
중곡동 중곡동
중곡동 중곡동
능동 능동
능동 능동
능동 능동
능동 능동
능동 능동
능동 능동
능동 능동
능동 능동
능동 능동
능동 능동
능동 능동
능동 능동
광장동 광장동
광장동 광장동
광장동 광장동
광장동 광장동
광장동 광장동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
자양동 자양동
화양동 화양동
화양동 화양동
화양동 화양동
군자동 군자동
군자동 군자동
군자동 군자동
군자동 군자동
군자동 군자동
군자동 군자동
군자동 군자동
군자동 군자동
신설동 신설동
용두동 용두동
용두동 용두동
용두동 용두동
용두동 용두동
용두동 용두동
용두동 용두동
용두동 용두동
용두동 용두동
용두동 용두동
용두동 용두동
제기동 제기동
제기동 제기동
제기동 제기동
제기동 제기동
제기동 제기동
제기동 제기동
제기동 제기동
제기동 제기동
제기동 제기동
제기동 제기동
제기동 제기동
전농동 전농동
전농동 전농동
전농동 전농동
전농동 전농동
전농동 전농동
전농동 전농동
전농동 전농동
답십리동 답십리동
답십리동 답십리동
답십리동 답십리동
답십리동 답십리동
답십리동 답십리동
답십리동 답십리동
답십리동 답십리동
답십리동 답십리동
답십리동 답십리동
답십리동 답십리동
답십리동 답십리동
답십리동 답십리동
답십리동 답십리동
답십리동 답십리동
답십리동 답십리동
답십리동 답십리동
장안동 장안동
장안동 장안동
장안동 장안동


망원동 망원동
망원동 망원동
망원동 망원동
연남동 연남동
연남동 연남동
연남동 연남동
연남동 연남동
연남동 연남동
연남동 연남동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
성산동 성산동
중동 중동
중동 중동
중동 중동
중동 중동
중동 중동
중동 중동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
신정동 신정동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
목동 목동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월동
신월동 신월

논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
논현동 논현동
세곡동 세곡동
일원동 일원동
일원동 일원동
일원동 일원동
일원동 일원동
일원동 일원동
일원동 일원동
일원동 일원동
일원동 일원동
도곡동 도곡동
도곡동 도곡동
도곡동 도곡동
도곡동 도곡동
도곡동 도곡동
잠실동 잠실동
잠실동 잠실동
잠실동 잠실동
잠실동 잠실동
잠실동 잠실동
잠실동 잠실동
잠실동 잠실동
잠실동 잠실동
잠실동 잠실동
잠실동 잠실동
잠실동 잠실동
잠실동 잠실동
잠실동 잠실동
잠실동 잠실동
잠실동 잠실동
잠실동 잠실동
풍납동 풍납동
풍납동 풍납동
풍납동 풍납동
풍납동 풍납동
풍납동 풍납동
풍납동 풍납동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
송파동 송파동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동
석촌동 석촌동


In [166]:
# dongCode 추가

address_list = get_address(seoul_code_list)
dong_list = list()
for a, row in df2.iterrows():
    for item in address_list:
        print(item[3])
        if str(row['지역코드']) == item[0] and str(row['법정동'] == item[3]):
            print('지역코드: ', row['지역코드'])
            print('######: ', item[0])
            print('법정동: ', row['법정동'])
            print('######: ', item[3])
            dong_list.append(item[2])
            break
#         elif str(row['지역코드']) == item[0] and str(row['법정동'] != item[3]):
#             print("?")
#         elif str(row['지역코드']) != item[0] and str(row['법정동'] == item[3]):
#             print("??")
#         else str(row['지역코드']) == item[0] and str(row['법정동'] != item[3]):
#             print("??")


지역코드:  11110
######:  11110
법정동:  청운동
######:  

지역코드:  11110
######:  11110
법정동:  청운동
######:  

지역코드:  11110
######:  11110
법정동:  효자동
######:  

지역코드:  11110
######:  11110
법정동:  통인동
######:  

지역코드:  11110
######:  11110
법정동:  누상동
######:  

지역코드:  11110
######:  11110
법정동:  누상동
######:  

지역코드:  11110
######:  11110
법정동:  누상동
######:  

지역코드:  11110
######:  11110
법정동:  누상동
######:  

지역코드:  11110
######:  11110
법정동:  누상동
######:  

지역코드:  11110
######:  11110
법정동:  옥인동
######:  

지역코드:  11110
######:  11110
법정동:  옥인동
######:  

지역코드:  11110
######:  11110
법정동:  필운동
######:  

지역코드:  11110
######:  11110
법정동:  삼청동
######:  

지역코드:  11110
######:  11110
법정동:  원서동
######:  

지역코드:  11110
######:  11110
법정동:  연건동
######:  

지역코드:  11110
######:  11110
법정동:  혜화동
######:  

지역코드:  11110
######:  11110
법정동:  혜화동
######:  

지역코드:  11110
######:  11110
법정동:  명륜1가
######:  

지역코드:  11110
######:  11110
법정동:  명륜3가
######:  

지역코드:  11110
######:  11110
법정동:  명륜3가
######:  

지역코드:  11110
###

당주동
내수동
세종로
신문로1가
신문로2가
청진동
서린동
수송동
중학동
종로1가
공평동
관훈동
견지동
와룡동
권농동
운니동
익선동
경운동
관철동
인사동
낙원동
종로2가
팔판동
삼청동
안국동
소격동
화동
사간동
송현동
가회동
재동
계동
원서동
훈정동
묘동
봉익동
돈의동
장사동
관수동
종로3가
인의동
예지동
원남동
연지동
종로4가
효제동
종로5가
종로6가
이화동
연건동
충신동
동숭동
혜화동
명륜1가
명륜2가
명륜4가
명륜3가
창신동
숭인동
교남동
평동
송월동
홍파동
교북동
행촌동
기동
평창동
부암동
홍지동
신영동
무악동
창신1동
창신2동
창신3동
숭인1동
숭인2동

지역코드:  11140
######:  11140
법정동:  신당동
######:  

청운동
신교동
궁정동
효자동
창성동
통의동
적선동
통인동
누상동
누하동
옥인동
체부동
필운동
내자동
사직동
도렴동
당주동
내수동
세종로
신문로1가
신문로2가
청진동
서린동
수송동
중학동
종로1가
공평동
관훈동
견지동
와룡동
권농동
운니동
익선동
경운동
관철동
인사동
낙원동
종로2가
팔판동
삼청동
안국동
소격동
화동
사간동
송현동
가회동
재동
계동
원서동
훈정동
묘동
봉익동
돈의동
장사동
관수동
종로3가
인의동
예지동
원남동
연지동
종로4가
효제동
종로5가
종로6가
이화동
연건동
충신동
동숭동
혜화동
명륜1가
명륜2가
명륜4가
명륜3가
창신동
숭인동
교남동
평동
송월동
홍파동
교북동
행촌동
기동
평창동
부암동
홍지동
신영동
무악동
창신1동
창신2동
창신3동
숭인1동
숭인2동

지역코드:  11140
######:  11140
법정동:  황학동
######:  

청운동
신교동
궁정동
효자동
창성동
통의동
적선동
통인동
누상동
누하동
옥인동
체부동
필운동
내자동
사직동
도렴동
당주동
내수동
세종로
신문로1가
신문로2가
청진동
서린동
수송동
중학동
종로1가
공평동
관훈동
견지동
와룡동
권농동
운니동
익선동
경운동
관철동
인사동
낙원동
종로2가
팔판동
삼청동
안국동
소격동
화동
사간동
송현동
가회동
재동
계동
원서동
훈정동

충신동
동숭동
혜화동
명륜1가
명륜2가
명륜4가
명륜3가
창신동
숭인동
교남동
평동
송월동
홍파동
교북동
행촌동
기동
평창동
부암동
홍지동
신영동
무악동
창신1동
창신2동
창신3동
숭인1동
숭인2동

동자동
도동1가
도동2가
양동
무교동
다동
태평로1가
을지로1가
을지로2가
남대문로1가
삼각동
수하동
장교동
수표동
소공동
남창동
북창동
태평로2가
남대문로2가
남대문로3가
남대문로4가
남대문로5가
봉래동1가
봉래동2가
회현동1가
회현동2가
회현동3가
충무로1가
충무로2가
명동1가
명동2가
남산동1가
남산동2가
남산동3가
저동1가
충무로4가
충무로5가
인현동2가
예관동
묵정동
필동1가
필동2가
필동3가
남학동
주자동
예장동
장충동1가
장충동2가
광희동1가
광희동2가
쌍림동
을지로6가
을지로7가
을지로4가
을지로5가
주교동
방산동
오장동
을지로3가
입정동
산림동
충무로3가
초동
인현동1가
저동2가
신당동
흥인동
무학동
황학동
서소문동
정동
순화동
의주로1가
충정로1가
중림동
의주로2가
만리동1가
만리동2가
신당1동
신당2동
신당3동
신당4동
신당5동
신당6동

지역코드:  11170
######:  11170
법정동:  용산동2가
######:  

청운동
신교동
궁정동
효자동
창성동
통의동
적선동
통인동
누상동
누하동
옥인동
체부동
필운동
내자동
사직동
도렴동
당주동
내수동
세종로
신문로1가
신문로2가
청진동
서린동
수송동
중학동
종로1가
공평동
관훈동
견지동
와룡동
권농동
운니동
익선동
경운동
관철동
인사동
낙원동
종로2가
팔판동
삼청동
안국동
소격동
화동
사간동
송현동
가회동
재동
계동
원서동
훈정동
묘동
봉익동
돈의동
장사동
관수동
종로3가
인의동
예지동
원남동
연지동
종로4가
효제동
종로5가
종로6가
이화동
연건동
충신동
동숭동
혜화동
명륜1가
명륜2가
명륜4가
명륜3가
창신동
숭인동
교남동
평동
송월동
홍파동
교북동
행촌동
기동
평창동
부암동
홍지동
신영동
무악동
창신1동
창신2동
창신3동
숭인1동
숭인2동

동자동
도동1가
도동2가
양동
무교동
다동
태

명동1가
명동2가
남산동1가
남산동2가
남산동3가
저동1가
충무로4가
충무로5가
인현동2가
예관동
묵정동
필동1가
필동2가
필동3가
남학동
주자동
예장동
장충동1가
장충동2가
광희동1가
광희동2가
쌍림동
을지로6가
을지로7가
을지로4가
을지로5가
주교동
방산동
오장동
을지로3가
입정동
산림동
충무로3가
초동
인현동1가
저동2가
신당동
흥인동
무학동
황학동
서소문동
정동
순화동
의주로1가
충정로1가
중림동
의주로2가
만리동1가
만리동2가
신당1동
신당2동
신당3동
신당4동
신당5동
신당6동

지역코드:  11170
######:  11170
법정동:  효창동
######:  

청운동
신교동
궁정동
효자동
창성동
통의동
적선동
통인동
누상동
누하동
옥인동
체부동
필운동
내자동
사직동
도렴동
당주동
내수동
세종로
신문로1가
신문로2가
청진동
서린동
수송동
중학동
종로1가
공평동
관훈동
견지동
와룡동
권농동
운니동
익선동
경운동
관철동
인사동
낙원동
종로2가
팔판동
삼청동
안국동
소격동
화동
사간동
송현동
가회동
재동
계동
원서동
훈정동
묘동
봉익동
돈의동
장사동
관수동
종로3가
인의동
예지동
원남동
연지동
종로4가
효제동
종로5가
종로6가
이화동
연건동
충신동
동숭동
혜화동
명륜1가
명륜2가
명륜4가
명륜3가
창신동
숭인동
교남동
평동
송월동
홍파동
교북동
행촌동
기동
평창동
부암동
홍지동
신영동
무악동
창신1동
창신2동
창신3동
숭인1동
숭인2동

동자동
도동1가
도동2가
양동
무교동
다동
태평로1가
을지로1가
을지로2가
남대문로1가
삼각동
수하동
장교동
수표동
소공동
남창동
북창동
태평로2가
남대문로2가
남대문로3가
남대문로4가
남대문로5가
봉래동1가
봉래동2가
회현동1가
회현동2가
회현동3가
충무로1가
충무로2가
명동1가
명동2가
남산동1가
남산동2가
남산동3가
저동1가
충무로4가
충무로5가
인현동2가
예관동
묵정동
필동1가
필동2가
필동3가
남학동
주자동
예장동
장충동1가
장충동2가
광희동1가
광희동2가
쌍림동
을지로6가
을지로7가
을지로4가
을지로5가
주

명륜2가
명륜4가
명륜3가
창신동
숭인동
교남동
평동
송월동
홍파동
교북동
행촌동
기동
평창동
부암동
홍지동
신영동
무악동
창신1동
창신2동
창신3동
숭인1동
숭인2동

동자동
도동1가
도동2가
양동
무교동
다동
태평로1가
을지로1가
을지로2가
남대문로1가
삼각동
수하동
장교동
수표동
소공동
남창동
북창동
태평로2가
남대문로2가
남대문로3가
남대문로4가
남대문로5가
봉래동1가
봉래동2가
회현동1가
회현동2가
회현동3가
충무로1가
충무로2가
명동1가
명동2가
남산동1가
남산동2가
남산동3가
저동1가
충무로4가
충무로5가
인현동2가
예관동
묵정동
필동1가
필동2가
필동3가
남학동
주자동
예장동
장충동1가
장충동2가
광희동1가
광희동2가
쌍림동
을지로6가
을지로7가
을지로4가
을지로5가
주교동
방산동
오장동
을지로3가
입정동
산림동
충무로3가
초동
인현동1가
저동2가
신당동
흥인동
무학동
황학동
서소문동
정동
순화동
의주로1가
충정로1가
중림동
의주로2가
만리동1가
만리동2가
신당1동
신당2동
신당3동
신당4동
신당5동
신당6동

지역코드:  11170
######:  11170
법정동:  한남동
######:  

청운동
신교동
궁정동
효자동
창성동
통의동
적선동
통인동
누상동
누하동
옥인동
체부동
필운동
내자동
사직동
도렴동
당주동
내수동
세종로
신문로1가
신문로2가
청진동
서린동
수송동
중학동
종로1가
공평동
관훈동
견지동
와룡동
권농동
운니동
익선동
경운동
관철동
인사동
낙원동
종로2가
팔판동
삼청동
안국동
소격동
화동
사간동
송현동
가회동
재동
계동
원서동
훈정동
묘동
봉익동
돈의동
장사동
관수동
종로3가
인의동
예지동
원남동
연지동
종로4가
효제동
종로5가
종로6가
이화동
연건동
충신동
동숭동
혜화동
명륜1가
명륜2가
명륜4가
명륜3가
창신동
숭인동
교남동
평동
송월동
홍파동
교북동
행촌동
기동
평창동
부암동
홍지동
신영동
무악동
창신1동
창신2동
창신3동
숭인1동
숭인2동

동자동
도동1가
도동2가
양동
무교동
다동
태평로1가
을지로1가
을지로2가
남대

...

삼선동3가
삼선동4가
삼선동5가
동선동1가
동선동2가
동선동3가
동선동4가
동선동5가
안암동1가
안암동2가
안암동3가
안암동4가
안암동5가
보문동4가
보문동5가
보문동6가
보문동7가
보문동1가
보문동2가
보문동3가
정릉동
길음동
종암동
하월곡동
상월곡동
장위동
석관동
성북1동
성북2동
삼선1동
삼선2동
동선1동
동선2동
돈암1동
돈암2동
정릉1동
정릉2동
정릉3동
정릉4동
길음1동
길음2동
길음3동
종암1동
종암2동
하월곡1동
하월곡2동
하월곡3동
하월곡4동
장위1동
장위2동
장위3동
석관1동
석관2동

미아동
번동
수유동
우이동

상계동
중계동
하계동
월계동
공릉동
미아동
번동
수유동
우이동
쌍문동
방학동
창동
도봉동
창1동
창2동
창3동
도봉1동
도봉2동
미아1동
미아2동
미아3동
미아4동
미아5동
미아6동
미아7동
미아8동
번1동
번2동
수유1동
수유2동
수유3동
수유4동
수유5동
쌍문1동
쌍문2동
쌍문3동
방학1동
방학2동
방학3동

창동
월계동
공릉동
하계동
상계동
중계동
도봉동
도봉1동
도봉2동
창1동
창2동
창3동
월계1동
월계2동
월계3동
공릉1동
공릉2동
상계1동
상계2동
상계3동
상계4동
상계5동
상계6동
상계7동

지역코드:  11380
######:  11380
법정동:  대조동
######:  

청운동
신교동
궁정동
효자동
창성동
통의동
적선동
통인동
누상동
누하동
옥인동
체부동
필운동
내자동
사직동
도렴동
당주동
내수동
세종로
신문로1가
신문로2가
청진동
서린동
수송동
중학동
종로1가
공평동
관훈동
견지동
와룡동
권농동
운니동
익선동
경운동
관철동
인사동
낙원동
종로2가
팔판동
삼청동
안국동
소격동
화동
사간동
송현동
가회동
재동
계동
원서동
훈정동
묘동
봉익동
돈의동
장사동
관수동
종로3가
인의동
예지동
원남동
연지동
종로4가
효제동
종로5가
종로6가
이화동
연건동
충신동
동숭동
혜화동
명륜1가
명륜2가
명륜4가
명륜3가
창신동
숭인동
교남동
평동
송월동
홍파동
교북동
행촌동
기동
평창동
부암동
홍지동
신영동
무악동
창신1동
창신2

회현동3가
충무로1가
충무로2가
명동1가
명동2가
남산동1가
남산동2가
남산동3가
저동1가
충무로4가
충무로5가
인현동2가
예관동
묵정동
필동1가
필동2가
필동3가
남학동
주자동
예장동
장충동1가
장충동2가
광희동1가
광희동2가
쌍림동
을지로6가
을지로7가
을지로4가
을지로5가
주교동
방산동
오장동
을지로3가
입정동
산림동
충무로3가
초동
인현동1가
저동2가
신당동
흥인동
무학동
황학동
서소문동
정동
순화동
의주로1가
충정로1가
중림동
의주로2가
만리동1가
만리동2가
신당1동
신당2동
신당3동
신당4동
신당5동
신당6동

옥수동
도동1가
도동2가
만리동1가
만리동2가
후암동
용산동2가
용산동4가
갈월동
남영동
용산동1가
동자동
서계동
청파동1가
청파동2가
청파동3가
원효로1가
원효로2가
신창동
산천동
청암동
원효로3가
원효로4가
효창동
도원동
용문동
문배동
신계동
한강로1가
한강로2가
용산동3가
용산동5가
한강로3가
이촌동
이태원동
한남동
동빙고동
서빙고동
주성동
용산동6가
보광동
청파1동
청파2동
이촌1동
이촌2동
이태원1동
이태원2동
한남1동
한남2동

상일동
길동
둔촌동
암사동
성내동
풍납동
천호동
송파동
석촌동
삼전동
가락동
이동
오금동
방이동
문정동
장지동
거여동
마천동
잠실동
신천동
일원동
수서동
자곡동
율현동
세곡동
역삼동
포이동
개포동
도곡동
논현동
신사동
학동
정동
청담동
삼성동
대치동
염곡동
내곡동
신원동
반포동
잠원동
서초동
양재동
우면동
원지동
황학동
무학동
흥인동
신당동
용두동
답십리동
면목동
금호동
명일동
하일동
고덕동
상왕십리동
하왕십리동
홍익동
도선동
마장동
사근동
행당동
응봉동
금호동1가
금호동2가
금호동3가
금호동4가
옥수동
성수동1가
성수동2가
화양동
모진동
송정동
군자동
중곡동
능동
용답동
광장동
의동
자양동
왕십리1동
왕십리2동
행당1동
행당2동
중곡1동
중곡2동
중곡3동
중곡4동
옥수1동
옥수2동
성수1가1동
성수1가2동
성수2가1동
성수2가2동
성수2가3동
성수2가4동
자양1동
자양2동
자양3동
의1동
의2동

중곡동


묵1동
묵2동
망우1동
망우2동
망우3동

미아동
번동
수유동
우이동
창동
월계동
쌍문동
공릉동
하계동
상계동
중계동
도봉동
방학동
성북동2가
동소문동8가
성북동
성북동1가
돈암동
동소문동1가
동소문동2가
동소문동3가
동소문동4가
동소문동5가
동소문동6가
동소문동7가
삼선동1가
삼선동2가
삼선동3가
삼선동4가
삼선동5가
동선동1가
동선동2가
동선동3가
동선동4가
동선동5가
안암동1가
안암동2가
안암동3가
안암동4가
안암동5가
보문동4가
보문동5가
보문동6가
보문동7가
보문동1가
보문동2가
보문동3가
정릉동
길음동
종암동
하월곡동
상월곡동
장위동
석관동
성북1동
성북2동
삼선1동
삼선2동
동선1동
동선2동
돈암1동
돈암2동
정릉1동
정릉2동
정릉3동
정릉4동
길음1동
길음2동
길음3동
종암1동
종암2동
하월곡1동
하월곡2동
하월곡3동
하월곡4동
장위1동
장위2동
장위3동
석관1동
석관2동

미아동
번동
수유동
우이동

상계동
중계동
하계동
월계동
공릉동
미아동
번동
수유동
우이동
쌍문동
방학동
창동
도봉동
창1동
창2동
창3동
도봉1동
도봉2동
미아1동
미아2동
미아3동
미아4동
미아5동
미아6동
미아7동
미아8동
번1동
번2동
수유1동
수유2동
수유3동
수유4동
수유5동
쌍문1동
쌍문2동
쌍문3동
방학1동
방학2동
방학3동

창동
월계동
공릉동
하계동
상계동
중계동
도봉동
도봉1동
도봉2동
창1동
창2동
창3동
월계1동
월계2동
월계3동
공릉1동
공릉2동
상계1동
상계2동
상계3동
상계4동
상계5동
상계6동
상계7동

지역코드:  11380
######:  11380
법정동:  대조동
######:  

청운동
신교동
궁정동
효자동
창성동
통의동
적선동
통인동
누상동
누하동
옥인동
체부동
필운동
내자동
사직동
도렴동
당주동
내수동
세종로
신문로1가
신문로2가
청진동
서린동
수송동
중학동
종로1가
공평동
관훈동
견지동
와룡동
권농동
운니동
익선동
경운동
관철동
인사동
낙원동
종로2가
팔판동
삼청동
안국동
소격동
화동
사간동
송현동
가회동
재동
계동
원서동
훈정동

원남동
연지동
종로4가
효제동
종로5가
종로6가
이화동
연건동
충신동
동숭동
혜화동
명륜1가
명륜2가
명륜4가
명륜3가
창신동
숭인동
교남동
평동
송월동
홍파동
교북동
행촌동
기동
평창동
부암동
홍지동
신영동
무악동
창신1동
창신2동
창신3동
숭인1동
숭인2동

동자동
도동1가
도동2가
양동
무교동
다동
태평로1가
을지로1가
을지로2가
남대문로1가
삼각동
수하동
장교동
수표동
소공동
남창동
북창동
태평로2가
남대문로2가
남대문로3가
남대문로4가
남대문로5가
봉래동1가
봉래동2가
회현동1가
회현동2가
회현동3가
충무로1가
충무로2가
명동1가
명동2가
남산동1가
남산동2가
남산동3가
저동1가
충무로4가
충무로5가
인현동2가
예관동
묵정동
필동1가
필동2가
필동3가
남학동
주자동
예장동
장충동1가
장충동2가
광희동1가
광희동2가
쌍림동
을지로6가
을지로7가
을지로4가
을지로5가
주교동
방산동
오장동
을지로3가
입정동
산림동
충무로3가
초동
인현동1가
저동2가
신당동
흥인동
무학동
황학동
서소문동
정동
순화동
의주로1가
충정로1가
중림동
의주로2가
만리동1가
만리동2가
신당1동
신당2동
신당3동
신당4동
신당5동
신당6동

옥수동
도동1가
도동2가
만리동1가
만리동2가
후암동
용산동2가
용산동4가
갈월동
남영동
용산동1가
동자동
서계동
청파동1가
청파동2가
청파동3가
원효로1가
원효로2가
신창동
산천동
청암동
원효로3가
원효로4가
효창동
도원동
용문동
문배동
신계동
한강로1가
한강로2가
용산동3가
용산동5가
한강로3가
이촌동
이태원동
한남동
동빙고동
서빙고동
주성동
용산동6가
보광동
청파1동
청파2동
이촌1동
이촌2동
이태원1동
이태원2동
한남1동
한남2동

상일동
길동
둔촌동
암사동
성내동
풍납동
천호동
송파동
석촌동
삼전동
가락동
이동
오금동
방이동
문정동
장지동
거여동
마천동
잠실동
신천동
일원동
수서동
자곡동
율현동
세곡동
역삼동
포이동
개포동
도곡동
논현동
신사동
학동
정동
청담동
삼성동
대치동
염곡동
내곡동
신원동
반포동
잠원동
서초동
양재동
우면동
원지동

KeyboardInterrupt: 

In [168]:
dong_list

['00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',
 '00000',


In [167]:
print(len(dong_list))

1047


In [147]:
'11200' in ('11200', '서울특별시 성동구', '11200', '금호동4가')

True

In [142]:
print(len(df2))

884618


In [141]:
# dongCode 추가

df2['dongCode'] = dong_list

ValueError: Length of values does not match length of index

In [12]:
# 예외 처리 방법
def get_jibunCode(jibun):
    if '-' in jibun:
        split_point = jibun.find('-')
        if len(jibun[:split_point]) == 1:
            if len(jibun[split_point+1:]) == 1:
                return '000'+jibun[:split_point]+'000'+jibun[split_point+1:]
            elif len(jibun[split_point+1:]) == 2:
                return '000'+jibun[:split_point]+'00'+jibun[split_point+1:]
            elif len(jibun[split_point+1:]) == 3:
                return '000'+jibun[:split_point]+'0'+jibun[split_point+1:]
            elif len(jibun[split_point+1:]) == 4:
                return '000'+jibun[:split_point]+jibun[split_point+1:]
        elif len(jibun[:split_point]) == 2:
            if len(jibun[split_point+1:]) == 1:
                return '00'+jibun[:split_point]+'000'+jibun[split_point+1:]
            elif len(jibun[split_point+1:]) == 2:
                return '00'+jibun[:split_point]+'00'+jibun[split_point+1:]
            elif len(jibun[split_point+1:]) == 3:
                return '00'+jibun[:split_point]+'0'+jibun[split_point+1:]
            elif len(jibun[split_point+1:]) == 4:
                return '00'+jibun[:split_point]+jibun[split_point+1:]
        elif len(jibun[:split_point]) == 3:
            if len(jibun[split_point+1:]) == 1:
                return '0'+jibun[:split_point]+'000'+jibun[split_point+1:]
            elif len(jibun[split_point+1:]) == 2:
                return '0'+jibun[:split_point]+'00'+jibun[split_point+1:]
            elif len(jibun[split_point+1:]) == 3:
                return '0'+jibun[:split_point]+'0'+jibun[split_point+1:]
            elif len(jibun[split_point+1:]) == 4:
                return '0'+jibun[:split_point]+jibun[split_point+1:]
        elif len(jibun[:split_point]) == 1:
            if len(jibun[split_point+1:]) == 4:
                return jibun[:split_point]+'000'+jibun[split_point+1:]
            elif len(jibun[split_point+1:]) == 2:
                return jibun[:split_point]+'00'+jibun[split_point+1:]
            elif len(jibun[split_point+1:]) == 3:
                return jibun[:split_point]+'0'+jibun[split_point+1:]
            elif len(jibun[split_point+1:]) == 4:
                return jibun[:split_point]+jibun[split_point+1:]
    else:
        if len(jibun) == 1:
            return '000'+jibun+'0000'
        elif len(jibun) == 2:
            return '00'+jibun+'0000'
        elif len(jibun) == 3:
            return '0'+jibun+'0000'
        elif len(jibun) == 4:
            return jibun+'0000'

In [45]:
# jibunCode 추가
df2['jibunCode'] = df2['지번'].map(get_jibunCode)

In [ ]:
# 최종 pnu 생성
df2['pnu'] = df2['지역코드'] + df2['dongCode'] + '1' + df2['jibunCode']

In [131]:
df2.drop

거래금액  건축년도     년   대지권면적   법정동         연립다세대   월      일    전용면적  \
0    57,000  2000  2017   45.98   청운동         귀빈하우스   1   1~10  102.40   
1    95,000  1988  2017  152.06   청운동       청운벽산빌리지   1  11~20  156.91   
2    38,000  2002  2017   48.97   효자동         씨티하우스   1  11~20   79.52   
3    54,000  2009  2017   34.42   통인동        씨에스코즈빌   1  21~31   74.91   
4     5,500  2001  2017    6.00   누상동       코디골든빌B동   1   1~10   17.11   
5    47,500  2003  2017   37.20   누상동       SM케슬빌리지   1   1~10   84.95   
6    49,200  2004  2017   41.54   누상동          동원빌라   1  11~20   80.06   
7    33,000  2004  2017   34.07   누상동          동원빌라   1  11~20   65.66   
8    40,000  2004  2017   35.96   누상동          동원빌라   1  11~20   69.30   
9    26,000  1997  2017   30.80   옥인동      (178-18)   1   1~10   49.73   
10   26,000  1997  2017   30.80   옥인동      (178-18)   1  11~20   49.73   
11   52,000  2002  2017   47.12   필운동          오성빌라   1  21~31   78.54   
12   49,700  2001  2017   57.79   삼청동      (35-149)   1  11~20   89.86   
13   40,000  2003  2017   29.59   원서동          진주빌라   1   1~10   70.32   
14    4,700  1995  2017   11.43   연건동        (88-1)   1   1~10   27.50   
15   43,000  1991  2017   91.31   혜화동      (15-172)   1  11~20  102.42   
16   77,000  2006  2017   88.41   혜화동       혜화노블하우스   1  11~20  150.23   
17   68,500  1990  2017  113.75  명륜1가         훼미리빌라   1  11~20  134.74   
18   25,000  2003  2017   42.07  명륜3가          명성빌라   1   1~10   60.77   
19   25,000  2003  2017   42.07  명륜3가          명성빌라   1   1~10   60.77   
20   27,500  2003  2017   51.83  명륜3가          명성빌라   1   1~10   74.88   
21   25,000  2003  2017   42.07  명륜3가          명성빌라   1   1~10   60.77   
22   27,500  2003  2017   51.83  명륜3가          명성빌라   1   1~10   74.88   
23   25,000  2003  2017   44.53  명륜3가          명성빌라   1   1~10   64.33   
24   15,000  1975  2017   38.45   창신동      (23-606)   1   1~10   52.69   
25   12,500  1998  2017   13.74   창신동       (616-6)   1  11~20   36.47   
26    8,000  1996  2017   12.56   창신동      (629-15)   1  11~20   25.10   
27   32,000  2002  2017   37.06   숭인동            이화   1   1~10   84.72   
28   16,500  2002  2017   16.60   숭인동       (908-0)   1   1~10   38.74   
29   33,800  2001  2017   31.21   숭인동       세원아트빌A동   1  11~20   84.56   
..      ...   ...   ...     ...   ...           ...  ..    ...     ...   
88   32,000  2017  2017   16.15   성내동         화영하우스  12  21~31   25.78   
89   25,400  2017  2017   16.60   성내동  아성플러스(37-79)  12  21~31   28.13   
90   25,700  2017  2017   16.86   성내동  아성플러스(37-79)  12  21~31   28.58   
91   25,000  2017  2017   16.60   성내동  아성플러스(37-79)  12  21~31   28.13   
92    8,050  2007  2017   16.52   천호동           센트빌  12   1~10   16.32   
93   17,800  1986  2017   32.22   천호동        초동빌라바동  12   1~10   41.67   
94   23,500  2008  2017   31.86   천호동      (314-23)  12   1~10   47.76   
95   12,000  1994  2017   25.84   천호동      (195-54)  12   1~10   33.24   
96   18,000  1986  2017   24.93   천호동        초동빌라가동  12   1~10   32.70   
97   22,000  2002  2017   32.18   천호동         은성빌리지  12   1~10   56.79   
98   33,500  2012  2017   32.06   천호동       아트쉐르빌6차  12   1~10   53.19   
99   25,000  2002  2017   26.24   천호동         청원그린빌  12   1~10   56.19   
100  20,000  1986  2017   23.61   천호동      (337-63)  12  11~20   33.67   
101  17,200  2011  2017   13.69   천호동    블루빌(25-32)  12  11~20   29.58   
102  15,400  2011  2017   16.60   천호동     신안아트빌(B동)  12  11~20   27.36   
103  22,500  2016  2017   10.18   천호동         주성아파텔  12  11~20   28.76   
104  22,000  2015  2017   13.40   천호동        SK힐하우스  12  11~20   20.14   
105  28,000  2016  2017   19.95   천호동         동림빌리지  12  11~20   29.79   
106  28,000  2016  2017   19.95   천호동         동림빌리지  12  11~20   29.79   
107  28,000  2016  2017   19.95   천호동         동림빌리지  12  11~20   29.79   
108  28,000  2016  2017   19.95   천호동         동림빌리지  12  11~20   29.79   
109  28,000  2016  2017   19.95   천호동         동림빌리지  12  11~20   29.79   
110  28,000

In [72]:
import os

# if not os.path.exists('/Users/jungwookim/dev/damta/real_estate/'):
#     os.makedirs('/Users/jungwookim/dev/damta/real_estate/')
    
with open('/Users/jungwookim/dev/RealEstateInSeoul/gongdong_price.csv', 'a') as f:
    
    '''
    pnu list를 일단 만들어내긴 해야한다. 무조건... 내 생각엔
    '''
    for code in code_dic:
        for page in range(1, 3):
            try:
                data_frame = get_gongdong_price('1111010100100040007', '2017', '100', page)
                data_frame = pd.DataFrame(df['apartHousingPrices']['field'])
                data_frame.to_csv(f, header=False, index_label = data_frame.columns)
                print(code, page)
            except:
                print("{} on {} PAGE NOT FOUND".format(code, page))
                continue

0     1111010100100040007
1     1111010100100040007
2     1111010100100040007
3     1111010100100040007
4     1111010100100040007
5     1111010100100040007
6     1111010100100040007
7     1111010100100040007
8     1111010200100170010
9     1111010500100980002
10    1111010900101510015
11    1111010900101660247
12    1111010900100330001
13    1111010900101200003
14    1111011100101830001
15    1111011500102620124
16    1111014000100350162
17    1111014800101400010
18    1111014900100770044
19    1111014900100860004
20    1111016800101290074
21    1111016800100040040
22    1111016900100050010
23    1111016900100100004
24    1111016900100220087
25    1111016900100050010
26    1111017000100450007
27    1111017000100050034
28    1111017000100430000
29    1111017000100160002
30    1111017100100860025
31    1111017300100010101
32    1111017400106390004
33    1111017400106270025
34    1111017400106400134
35    1111017500101780135
36    1111017500100720048
37    1111017500108200000
38    111101

In [ ]:
df = get_gongdong_price('1111010100100040007', '2017', '10', '1')
df = pd.DataFrame(df['apartHousingPrices']['field'])
df.head()